In [175]:
from optimize_model import optimize_model
from cobra_utils import print_logo, load_model, set_default_bounds, \
    convert_model_format, fetch_norm_sample_metabolomics_data, match_names_to_vmh

# Define paths
json_model_path = "example_data/models/microbiota_model_diet_Case_1_18_month.json"
matlab_model_path = "example_data/models/microbiota_model_diet_Case_1_18_month.mat"
metabolomics_path = "example_data/metabolomics_data.csv"
avg_eu_diet_path = "example_data/AverageEU_diet_fluxes.txt"

# Load the model
model = load_model(json_model_path)

# Get the model-specific metabolomics data
gcms_metab_norm = fetch_norm_sample_metabolomics_data(model_input=model, gcms_filepath=metabolomics_path, match_key_output_filepath="example_outputs", use_existing_matched_keys=True, existing_keys_path="example_outputs/")


[START] Loading model from example_data/models/microbiota_model_diet_Case_1_18_month.json...

[DONE] microbiota_model_diet_Case_1_18_month loaded.

[START] Fetching metabolomics data for microbiota_model_diet_Case_1_18_month...

Number of VMH ID-matched metabolites: 48 of 63

[DONE] Returning normalized sample-specific metabolomics values for Case_1.


In [176]:
rxn_id_gcms_val = {f"UFEt_{metab}": gcms_value for metab, gcms_value in gcms_metab_norm.items() if f"UFEt_{metab}" in model.reactions and gcms_value != 0}

In [177]:
total = sum(rxn_id_gcms_val.values())
normalized_gcms_metab_vals = {k: v / total for k, v in rxn_id_gcms_val.items()}

assert sum(normalized_gcms_metab_vals.values()) == 1

In [178]:
# Calculate the constraint for each metabolite's UFEt reactions
metab_constrained_flux_expr = dict()
for vmh_id, gcms_value in gcms_metab_norm.items():
    if gcms_value != 0. and f"UFEt_{vmh_id}" in model.reactions:
        metab_constrained_flux_expr[f"UFEt_{vmh_id}"] = gcms_value*sum(model.reactions.get_by_id(f"UFEt_{metab}").flux_expression for metab in gcms_metab_norm.keys() if f"UFEt_{metab}" in model.reactions)

In [179]:
metab_constrained_flux_expr

{'UFEt_mal_L': 0.0103740189995354*UFEt_M03134 - 0.0103740189995354*UFEt_M03134_reverse_020ec + 0.0103740189995354*UFEt_acgal - 0.0103740189995354*UFEt_acgal_reverse_dbec8 + 0.0103740189995354*UFEt_arab_L - 0.0103740189995354*UFEt_arab_L_reverse_4baab + 0.0103740189995354*UFEt_asp_L - 0.0103740189995354*UFEt_asp_L_reverse_a4a74 + 0.0103740189995354*UFEt_but - 0.0103740189995354*UFEt_but_reverse_d155e + 0.0103740189995354*UFEt_bz - 0.0103740189995354*UFEt_bz_reverse_bcab0 + 0.0103740189995354*UFEt_drib - 0.0103740189995354*UFEt_drib_reverse_4819b + 0.0103740189995354*UFEt_fru - 0.0103740189995354*UFEt_fru_reverse_1d253 + 0.0103740189995354*UFEt_gal - 0.0103740189995354*UFEt_gal_reverse_ccbd3 + 0.0103740189995354*UFEt_glc_D - 0.0103740189995354*UFEt_glc_D_reverse_374a6 + 0.0103740189995354*UFEt_glcn - 0.0103740189995354*UFEt_glcn_reverse_e5fef + 0.0103740189995354*UFEt_gly - 0.0103740189995354*UFEt_gly_reverse_24715 + 0.0103740189995354*UFEt_glyc - 0.0103740189995354*UFEt_glyc_reverse_a24

In [180]:
model.reactions.get_by_id("UFEt_xyl_D")

<Reaction UFEt_xyl_D at 0x2f36e5c10>

In [181]:
# Add the constraints to the model for each metabolite
constraint_list = []
for metab_rxn, flux_expr in metab_constrained_flux_expr.items():
    constraint = model.problem.Constraint(flux_expr, lb=0., ub=1000000., name=metab_rxn)
    constraint_list.append(constraint)
model.add_cons_vars(constraint_list)
model.solver.update()

In [214]:
for rxn_name in metab_constrained_flux_expr.keys():
    model.objective = model.reactions.get_by_id(rxn_name)
    solution = model.optimize()
    print(f"\n{model.reactions.get_by_id(rxn_name)}:\t{solution.objective_value}")


UFEt_mal_L: mal_L[u] --> mal_L[fe]:	137.9025816841263

UFEt_lac_D: lac_D[u] --> lac_D[fe]:	1661.4444775826983

UFEt_drib: drib[u] --> drib[fe]:	0.1

UFEt_rib_D: rib_D[u] --> rib_D[fe]:	0.1

UFEt_fru: fru[u] --> fru[fe]:	687.4114008137759

UFEt_gal: gal[u] --> gal[fe]:	9.326699999999999

UFEt_acgal: acgal[u] --> acgal[fe]:	17.0

UFEt_arab_L: arab_L[u] --> arab_L[fe]:	1.0

UFEt_glc_D: glc_D[u] --> glc_D[fe]:	297.433

UFEt_gly: gly[u] --> gly[fe]:	20.1

UFEt_glyc: glyc[u] --> glyc[fe]:	0.15589915568122498

UFEt_M03134: M03134[u] --> M03134[fe]:	0.0

UFEt_man: man[u] --> man[fe]:	0.1

UFEt_pro_L: pro_L[u] --> pro_L[fe]:	229.8580626352488

UFEt_ser_L: ser_L[u] --> ser_L[fe]:	0.19054341447057171

UFEt_asp_L: asp_L[u] --> asp_L[fe]:	47.0867

UFEt_but: but[u] --> but[fe]:	26.3343

UFEt_bz: bz[u] --> bz[fe]:	0.0

UFEt_glcn: glcn[u] --> glcn[fe]:	0.1

UFEt_hdca: hdca[u] --> hdca[fe]:	0.1

UFEt_ocdca: ocdca[u] --> ocdca[fe]:	0.09775646128896001

UFEt_succ: succ[u] --> succ[fe]:	1374.116702136159

In [210]:
for k, v in model.constraints.items():
    print(k, v)

12ppd_S[d] 12ppd_S[d]: 0 <= -1.0*DUt_12ppd_S + 1.0*DUt_12ppd_S_reverse_84ac8 - 1.0*Diet_EX_12ppd_S[d] + 1.0*Diet_EX_12ppd_S[d]_reverse_feb0c <= 0
12ppd_S[fe] 12ppd_S[fe]: 0 <= -1.0*EX_12ppd_S[fe] + 1.0*EX_12ppd_S[fe]_reverse_89afb + 1.0*UFEt_12ppd_S - 1.0*UFEt_12ppd_S_reverse_6a4ae <= 0
12ppd_S[u] 12ppd_S[u]: 0 <= -1.0*Bacteroides_cellulosilyticus_DSM_14838_IEX_12ppd_S[u]tr + 1.0*Bacteroides_cellulosilyticus_DSM_14838_IEX_12ppd_S[u]tr_reverse_e487b - 1.0*Bacteroides_ovatus_ATCC_8483_IEX_12ppd_S[u]tr + 1.0*Bacteroides_ovatus_ATCC_8483_IEX_12ppd_S[u]tr_reverse_b595a - 1.0*Bacteroides_vulgatus_ATCC_8482_IEX_12ppd_S[u]tr + 1.0*Bacteroides_vulgatus_ATCC_8482_IEX_12ppd_S[u]tr_reverse_613a2 + 1.0*DUt_12ppd_S - 1.0*DUt_12ppd_S_reverse_84ac8 - 1.0*Parabacteroides_merdae_ATCC_43184_IEX_12ppd_S[u]tr + 1.0*Parabacteroides_merdae_ATCC_43184_IEX_12ppd_S[u]tr_reverse_1cf80 - 1.0*UFEt_12ppd_S + 1.0*UFEt_12ppd_S_reverse_6a4ae <= 0
1hibup_S[d] 1hibup_S[d]: 0 <= -1.0*DUt_1hibup_S + 1.0*DUt_1hibup_S_rever